# Austin Animal Center Shelter - Plotly Summer Challenge

## Imports

In [81]:
import pandas as pd
import numpy as np
from AAC_challenge import data
from AAC_challenge import plots

import plotly as plt
import seaborn as sns
import plotly.express as px

import warnings
warnings.filterwarnings('ignore')

%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


## Data loading and basic cleaning

In [89]:
aac_eng_df = data.get_clean_cat_dataset('cats')

In [91]:
aac_eng_df

animal_id                breed         color date_of_birth  \
0       A684346   domestic shorthair        orange    2014-07-07   
1       A685067   domestic shorthair   blue /white    2014-06-16   
2       A678580   domestic shorthair   white/black    2014-03-26   
3       A675405  domestic mediumhair   black/white    2013-03-27   
4       A670420   domestic shorthair   black/white    2013-12-16   
...         ...                  ...           ...           ...   
29406   A758112   american shorthair   blue /white    2017-09-14   
29407   A758569   domestic shorthair  brown /white    2017-08-03   
29408   A765938   domestic shorthair         brown    2017-01-30   
29409   A765832   domestic shorthair         brown    2017-07-28   
29410   A765831  domestic mediumhair        orange    2017-07-28   

      outcome_datetime     outcome_type  sex  sterilized periods period_range  \
0           2014-07-22         Transfer    0           0       2            7   
1           2014-08-14         Adoption    1           0       1           30   
2           2014-06-29         Adoption    1           1       3           30   
3           2014-03-28  Return to Owner    1           1       1          365   
4           2014-01-09         Transfer    0           0       3            7   
...                ...              ...  ...         ...     ...          ...   
29406       2017-12-10         Adoption    1           0       2           30   
29407       2017-09-24         Adoption    0           0       1           30   
29408       2018-02-01         Transfer    0           1       1          365   
29409       2018-02-01         Adoption    1           1       6           30   
29410       2018-02-01         Adoption    0           1       6           30   

       ... cfa_breed domestic_breed  coat_pattern      main_color    coat  \
0      ...         0              1         tabby          orange  orange   
1      ...         0              1         tabby           blue     blue   
2      ...         0              1         tabby           white   white   
3      ...         0              1         tabby           black   black   
4      ...         0              1         tabby           black   black   
...    ...       ...            ...           ...             ...     ...   
29406  ...         1              0         tabby           blue     blue   
29407  ...         0              1         tabby          brown    brown   
29408  ...         0              1         tabby           brown   brown   
29409  ...         0              1        tortie  Breed Specific  tortie   
29410  ...         0              1         tabby          orange  orange   

      has_name           top_breeds  top_coats adopted_or_not  \
0            0   domestic shorthair     orange              0   
1            1   domestic shorthair       blue              1   
2            1   domestic shorthair      white              1   
3            1  domestic mediumhair      black              0   
4            0   domestic shorthair      black              0   
...        ...                  ...        ...            ...   
29406        1   american shorthair       blue              1   
29407        1   domestic shorthair      brown              1   
29408        0   domestic shorthair      brown              0   
29409        1   domestic shorthair     tortie              1   
29410        1  domestic mediumhair     orange              1   

      outcome_year_month  
0             2014-07-01  
1             2014-08-01  
2             2014-06-01  
3             2014-03-01  
4             2014-01-01  
...                  ...  
29406         2017-12-01  
29407         2017-09-01  
29408         2018-02-01  
29409         2018-02-01  
29410         2018-02-01  

[29411 rows x 26 columns]

## Get and clean intake data

In [92]:
intakes_df = data.load_csv('intakes')
intakes_df = data.clean_intake_dataset(intakes_df, 'cats')
intakes_df.head()

animal_id         intake_datetime intake_month_year  \
3    A665644  10/21/2013 07:59:00 AM      October 2013   
7    A844350  10/15/2021 11:40:00 AM      October 2021   
9    A818975  06/18/2020 02:53:00 PM         June 2020   
10   A774147  06/11/2018 07:45:00 AM         June 2018   
11   A731435  08/08/2016 05:52:00 PM       August 2016   

                                   found_location      intake_type  \
3                                     Austin (TX)            Stray   
7   2112 East William Cannon Drive in Austin (TX)            Stray   
9           Braker Lane And Metric in Travis (TX)            Stray   
10                  6600 Elm Creek in Austin (TX)            Stray   
11                                    Austin (TX)  Owner Surrender   

   intake_condition age_upon_intake  has_name  sex_intake  sterilized_intake  
3              Sick         4 weeks         0           1                  0  
7            Normal        6 months         1           1                  0  
9            Normal         4 weeks         0           0                  0  
10          Injured         4 weeks         0           1                  0  
11           Normal        5 months         1           0                  1

## Merge outcomes to intakes on animal_id

In [115]:
merged_df = aac_eng_df.merge(intakes_df, how='left', on='animal_id')
merged_df.shape

(32373, 35)

In [158]:
merged_df = data.merge_intakes_outcomes()
merged_df.head(3)

animal_id               breed        color date_of_birth outcome_datetime  \
0   A684346  domestic shorthair       orange    2014-07-07       2014-07-22   
1   A685067  domestic shorthair  blue /white    2014-06-16       2014-08-14   
2   A678580  domestic shorthair  white/black    2014-03-26       2014-06-29   

  outcome_type  sex  sterilized_outcome periods period_range  ...  \
0     Transfer    0                   0       2            7  ...   
1     Adoption    1                   0       1           30  ...   
2     Adoption    1                   1       3           30  ...   

  outcome_year_month intake_datetime  intake_month_year  \
0         2014-07-01      2014-07-22          July 2014   
1         2014-08-01      2014-08-01        August 2014   
2         2014-06-01      2014-05-10           May 2014   

                       found_location intake_type intake_condition  \
0    45065 Felicity Ln in Austin (TX)       Stray          Nursing   
1  1901 Crossing Place in Austin (TX)       Stray           Normal   
2         7707 S Ih 35 in Austin (TX)       Stray           Normal   

   intake_age_days  sterilized_intake days_spent_at_shelter age_diff_days  
0             14.0                0.0                     0           0.0  
1             30.0                0.0                    13           0.0  
2             30.0                0.0                    50          60.0  

[3 rows x 35 columns]

In [159]:
merged_df[merged_df.days_spent_at_shelter < 0]

animal_id                     breed          color date_of_birth  \
6       A684460        domestic shorthair          brown    2014-06-02   
28      A670656        domestic shorthair    blue /white    2008-01-11   
30      A670656        domestic shorthair    blue /white    2008-01-11   
36      A688036        domestic shorthair           blue    2012-09-13   
40      A691706         domestic longhair          brown    2014-10-01   
...         ...                       ...            ...           ...   
32291   A765350        domestic shorthair           gray    2017-03-18   
32301   A762929  domestic mediumhair/manx    white/white    2009-11-30   
32310   A763036        domestic shorthair   brown /white    2017-11-06   
32318   A758827        domestic shorthair  orange /white    2014-09-22   
32334   A350276                abyssinian        brown /    2004-04-13   

      outcome_datetime     outcome_type  sex  sterilized_outcome periods  \
6           2014-08-13         Adoption    1                   1       2   
28          2014-01-17  Return to Owner    0                   1       6   
30          2014-01-17  Return to Owner    0                   1       6   
36          2014-09-14         Transfer    0                   1       2   
40          2014-12-13         Adoption    1                   1       2   
...                ...              ...  ...                 ...     ...   
32291       2018-01-27         Adoption    0                   1      10   
32301       2018-01-28         Adoption    0                   1       8   
32310       2018-01-14         Adoption    0                   1       2   
32318       2018-01-29         Adoption    0                   1       3   
32334       2018-01-28         Adoption    1                   1      13   

      period_range  ... outcome_year_month intake_datetime  intake_month_year  \
6               30  ...         2014-08-01      2015-11-05      November 2015   
28             365  ...         2014-01-01      2015-05-04           May 2015   
30             365  ...         2014-01-01      2014-10-20       October 2014   
36             365  ...         2014-09-01      2014-09-16     September 2014   
40              30  ...         2014-12-01      2017-09-30     September 2017   
...            ...  ...                ...             ...                ...   
32291           30  ...         2018-01-01      2018-01-29       January 2018   
32301          365  ...         2018-01-01      2018-06-25          June 2018   
32310           30  ...         2018-01-01      2018-01-28       January 2018   
32318          365  ...         2018-01-01      2018-06-12          June 2018   
32334          365  ...         2018-01-01      2019-12-21      December 2019   

                  found_location      intake_type intake_condition  \
6                    Austin (TX)  Owner Surrender           Normal   
28                   Austin (TX)  Owner Surrender           Normal   
30                Del Valle (TX)  Owner Surrender           Normal   
36     3201 Duval in Austin (TX)            Stray           Normal   
40                   Austin (TX)  Owner Surrender           Normal   
...                          ...              ...              ...   
32291                Austin (TX)  Owner Surrender           Normal   
32301                Austin (TX)  Owner Surrender           Normal   
32310                Austin (TX)  Owner Surrender           Normal   
32318                Austin (TX)  Owner Surrender           Normal   
32334                Austin (TX)  Owner Surrender           Normal   

       intake_age_days  sterilized_intake days_spent_at_shelter age_diff_days  
6                365.0                1.0                  -449        -305.0  
28              2555.0                1.0                  -472        -365.0  
30              2190.0                1.0                  -276           0.0  
36               730.0                1.0                    -2       

## Basic data visualization

### `coat` and `sex`


The four most common coats are `black`, `brown`, `blue`, and `orange` and fairly even between male and female.

The coats `tortie` and `calico` are exclusively females.

In [118]:
coats_sorted = merged_df.groupby('coat', as_index=False).count()[['coat', 'sex']].sort_values('sex', ascending=False)
top_coats = list(coats_sorted[coats_sorted['sex'] >= 100]['coat'])

In [156]:
fig = px.histogram(merged_df, x="days_spent_at_shelter", color = 'sex', title= "All outcomes")
fig.show()

In [52]:
fig = px.histogram(aac_eng_adopted, x="coat", color = 'sex', title= "Adoptions only")
fig.show()

In [120]:
fig = px.histogram(merged_df, x="coat_pattern", color = 'adopted_or_not', title= "Adopted or not")
fig.show()

In [121]:
fig = px.histogram(merged_df, x="cfa_breed", color = 'adopted_or_not', title= "Adopted or not")
fig.show()

In [122]:
fig = px.histogram(merged_df, x="domestic_breed", color = 'adopted_or_not', title= "adopted_or_not")
fig.show()

### `age`

Most outcomes are less than `6 months` old and exponentially decrease with age. Across all ages, outcomes are fairly evenly distributed between male and female.

In [124]:
plots.get_outcome_age_histogram(merged_df)

In [125]:
plots.get_outcome_age_histogram(aac_eng_df, adoptions_only=True)

### `sterilized` 

Outcomes are primarily transfers and adoptions. For adoptions, 90% of the cats are spayed/neutered.

In [126]:
plots.get_outcome_sterilized_histogram(aac_eng_df)

### `outcome_weekday`

In [127]:
plots.get_outcome_weekday_histogram(aac_eng_df)

**Overall, there are more adoptions on Saturdays (and Sundays) and less adoptions on Thurdays.**

### `breed`

In [128]:
plots.get_top_breeds_pie(merged_df, adoptions_only=True)

### `outcome_datetime`

Adoptions periodically peak in `July` and are the lowest in `March/April`.

In [129]:
plots.get_outcome_timeseries(merged_df)

### `has_name`

**Most cats adopted have names!!**

In [130]:
plots.get_has_name_histogram(merged_df)

## EDA summary

* There are as much males as there are females;
* Adoptions represent around 43% of all outcomes;
* The great majority of adopted cats are spayed/neutered and have a name;
* The most cats (therefore most adopted) have black, brown, and blue coats;
* The great majority of cats (therefore adopted cats) are 0 to 6 months old;
* There are more adoptions on Saturdays (and Sundays) and less on Thurdays;
* The most represented breeds of cats are domestic short hair, medium hair, long hair, and siamese;
* Adoptions peak in June/July and are the lowest in March/April;

**Next step -> transfer cleaning and plotting code to VS code** OK

**Next step -> suggest actions to increase chances of adoption**

**Next step -> predict outcome 1 if adopted else 0**